In [1]:
import pandas as pd
import numpy as np
import math as mt
import streamlit as st
import plotly.express as px

In [2]:
# Import Data
df = pd.read_csv('vehicles_us.csv')

In [3]:
# EDA
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


**Initial Observations**
- `Model_year`, `cylinders`, `odometer`, `paint_color`, and `is_4wd` have null values.
-All null value columns except `is_4wd` can be filled with N/A. `is_4wd` can be filled with zero to indicate no 4-wheel drive
- `Model` column currently contains the make and model of the car in the same value. Would be better to split this in to `Make` and `Model` columns so better analysis can be performed.

In [4]:
df.head(10)

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   
5  14990      2014.0    chrysler 300  excellent        6.0  gas   57954.0   
6  12990      2015.0    toyota camry  excellent        4.0  gas   79212.0   
7  15990      2013.0     honda pilot  excellent        6.0  gas  109473.0   
8  11500      2012.0     kia sorento  excellent        4.0  gas  104174.0   
9   9200      2008.0     honda pilot  excellent        NaN  gas  147191.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28  
5    automatic   sedan       black     1.0  2018-06-20           15  
6    automatic   sedan       white     NaN  2018-12-27           73  
7    automatic     SUV       black     1.0  2019-01-07           68  
8    automatic     SUV         NaN     1.0  2018-07-16           19  
9    automatic     SUV        blue     1.0  2019-02-15           17

In [5]:
# Rename model column to make_model to prepare for change
df = df.rename(columns={'model':'make_model'})
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   make_model    51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [6]:
#Check cell for comparison later
df['make_model'].head(10)

0            bmw x5
1        ford f-150
2    hyundai sonata
3        ford f-150
4      chrysler 200
5      chrysler 300
6      toyota camry
7       honda pilot
8       kia sorento
9       honda pilot
Name: make_model, dtype: object

In [7]:
# Get unique values from the model category
df['make_model'].unique()

array(['bmw x5', 'ford f-150', 'hyundai sonata', 'chrysler 200',
       'chrysler 300', 'toyota camry', 'honda pilot', 'kia sorento',
       'chevrolet silverado 1500', 'honda accord', 'ram 1500',
       'gmc yukon', 'jeep cherokee', 'chevrolet traverse',
       'hyundai elantra', 'chevrolet tahoe', 'toyota rav4',
       'chevrolet silverado', 'jeep wrangler', 'chevrolet malibu',
       'ford fusion se', 'chevrolet impala', 'chevrolet corvette',
       'jeep liberty', 'toyota camry le', 'nissan altima',
       'subaru outback', 'toyota highlander', 'dodge charger',
       'toyota tacoma', 'chevrolet equinox', 'nissan rogue',
       'mercedes-benz benze sprinter 2500', 'honda cr-v',
       'jeep grand cherokee', 'toyota 4runner', 'ford focus',
       'honda civic', 'kia soul', 'chevrolet colorado',
       'ford f150 supercrew cab xlt', 'chevrolet camaro lt coupe 2d',
       'chevrolet cruze', 'ford mustang', 'chevrolet silverado 3500hd',
       'nissan frontier crew cab sv', 'subaru imp

In [8]:
# Split items in make_model column and assign them to individual make and model columns
df['make'] = df['make_model'].str.split().str[0]
df['model'] = df['make_model'].str.split().str[1:]
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 15 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   make_model    51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
 13  make          51525 non-null  object 
 14  model         51525 non-null  object 
dtypes: float64(4), int64(2), object(9)
memory usage: 5.9+ MB


In [9]:
# Above change leaves the model column as a series of lists. Below will concatenate the lists into single spaced strings
df['model'] = df['model'].apply(lambda x:' '.join(x))
df['model'].head(10)

0         x5
1      f-150
2     sonata
3      f-150
4        200
5        300
6      camry
7      pilot
8    sorento
9      pilot
Name: model, dtype: object

In [10]:
# Fill null values in is_4wd column with 0.00 to indicate no 4-wheel drive
df['is_4wd'] = df['is_4wd'].fillna(0.0)

#Check for duplicated rows
print(df.duplicated().unique())

#Check vehicle info again
print(df.info())

[False]
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 15 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   make_model    51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        51525 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
 13  make          51525 non-null  object 
 14  model         51525 non-null  object 
dtypes: float64(4), int64(2), object(9)
memory usage: 5.9+ MB
None


In [11]:
# Data Viewer
st.header('Data viewer') 
st.dataframe(df)

# Create Vehicle types by manufacturer histogram
st.header('Vehicle type by Manufactuer')
fig = px.histogram(df, x='make',color='type')
st.write(fig)
fig


2024-06-28 22:29:55.871 
  command:

    streamlit run C:\Users\colin\AppData\Roaming\Python\Python312\site-packages\ipykernel_launcher.py [ARGUMENTS]


In [12]:
# Create Price Vs Color
st.header('Price by vehicle color')
color_map = df['paint_color'].unique()
fig = px.histogram(df, x='paint_color', y='price', 
                   color='paint_color',
                   color_discrete_map={'white':'white','red':'red','black':'black', 'blue':'blue', 'grey':'grey', 'silver':'silver', 'custom':'teal', 'orange':'orange', 'yellow':'yellow', 'brown':'brown', 'green':'green', 'purple':'purple'},
                   labels={'price':'price ($)','paint_color':'vehicle color'})
fig.update_layout(plot_bgcolor = 'tan')
fig

In [13]:
# Create price distribution
st.header('Compare price distribution between manufacturers')
# get a list of car manufacturers
manufac_list = sorted(df['make'].unique())
# get user's inputs from a dropdown menu
manufacturer_1 = st.selectbox(
                              label='Select Manufacturer 1', # title of the select box
                              options=manufac_list, # options listed in the select box
                              index=manufac_list.index('chevrolet') # default pre-selected option
                              )
# repeat for the second dropdown menu
manufacturer_2 = st.selectbox(
                              label='Select Manufacturer 2',
                              options=manufac_list, 
                              index=manufac_list.index('hyundai')
                              )
# filter the dataframe 
mask_filter = (df['make'] == manufacturer_1) | (df['make'] == manufacturer_2)
df_filtered = df[mask_filter]

# add a checkbox if a user wants to normalize the histogram
normalize = st.checkbox('Normalize histogram', value=True)
if normalize:
    histnorm = 'percent'
else:
    histnorm = None

In [ ]:
# Create Various Price Scatter
st.header('Price Scatter by Various')
x_list = ['model_year','odometer','days_listed']
x_select = st.selectbox(
                        label='Select data',
                        options=x_list,
                        index=x_list.index('model_year')
)
# Select Unique Options for each scatter plot
if x_select == 'model_year':
    color_select = ['blue']
    title_select = 'Price by Vehicle Year'
    label_select = {'price':'Price ($)','model_year':'Vehicle Year'}
elif x_select == 'odometer':
    color_select = ['green']
    title_select = 'Price by Mileage'
    label_select = {'price':'Price ($)','odometer':'Mileage (mi)'}
elif x_select == 'days_listed':
    color_select = ['brown']
    title_select = 'Price by Time Listed'
    label_select = {'price':'Price ($)','days_listed':'No. Days Listed'}
# Create Scatterplots
fig = px.scatter(df, x=x_select, y='price',
                 color_discrete_sequence=color_select,
                 title=title_select,
                 labels=label_select
                )
fig.show()

In [21]:
df.columns

Index(['price', 'model_year', 'make_model', 'condition', 'cylinders', 'fuel',
       'odometer', 'transmission', 'type', 'paint_color', 'is_4wd',
       'date_posted', 'days_listed', 'make', 'model'],
      dtype='object')